In [ ]:
#this script will scrape the data for every player for every game for the provided season. 

In [ ]:
#this is likely the endpoint we will use:
from nba_api.stats.endpoints import leaguegamefinder
from sqlalchemy import create_engine
from requests.exceptions import ReadTimeout
import pandas as pd
import random
import time 
import json

#create our engine for pushing to sql database
from dotenv import load_dotenv
import os

load_dotenv()

DATABASE_URL = os.getenv("DATABASE_URL")

engine = create_engine(DATABASE_URL)

#define seasons to gather data for 
seasons = ['2022-23', '2023-24', '2024-25']

for season in seasons:
    try:
        # Get all games for a season
        game_finder = leaguegamefinder.LeagueGameFinder(
            season_nullable=season,  # Format: YYYY-YY
            league_id_nullable='00',    # 00 is NBA
            season_type_nullable='Regular Season'  # or 'Playoffs'
        )
        
        # Convert to DataFrame
        games_df = game_finder.get_data_frames()[0]
        
        #make team ID the index, and sort the dataframe based on ID and gameDate
        games_df = games_df.set_index('TEAM_ID')
        games_df_sorted = games_df.sort_values(['TEAM_ID', 'GAME_DATE'], ascending=[True, False])
    
        #once we've created the dataframe, we want to push that to a SQL database
        filename = f"{season}_historic_game_data"
        games_df_sorted.to_sql(filename, engine, if_exists='replace', index=True)
        print(f"Created and stored dataframe for {season} season")
        print()
        time.sleep(round(random.uniform(3, 6), 1))

    #handle timeout/api rejection errors
    except (ReadTimeout, json.decoder.JSONDecodeError) as e:
        print(f"Error for {season}: {e} - retrying after 60 seconds")
        time.sleep(60)
        continue

print("Finished data gathering for specified seasons")

Created and stored dataframe for 2022-23 season

Created and stored dataframe for 2023-24 season

Created and stored dataframe for 2024-25 season

Finished data gathering for specified seasons


In [11]:
games_df_sorted

SEASON_ID TEAM_ABBREVIATION          TEAM_NAME     GAME_ID  \
TEAM_ID                                                                 
1610612737     22024               ATL      Atlanta Hawks  0022400656   
1610612737     22024               ATL      Atlanta Hawks  0022400639   
1610612737     22024               ATL      Atlanta Hawks  0022400623   
1610612737     22024               ATL      Atlanta Hawks  0022400612   
1610612737     22024               ATL      Atlanta Hawks  0022400602   
...              ...               ...                ...         ...   
1610612766     22024               CHA  Charlotte Hornets  0022400132   
1610612766     22024               CHA  Charlotte Hornets  0022400117   
1610612766     22024               CHA  Charlotte Hornets  0022400088   
1610612766     22024               CHA  Charlotte Hornets  0022400079   
1610612766     22024               CHA  Charlotte Hornets  0022400068   

             GAME_DATE      MATCHUP WL  MIN  PTS  FGM  ...  FT_PCT  OREB  \
TEAM_ID                                                ...                 
1610612737  2025-01-27    ATL @ MIN  L  241   92   34  ...   0.667    14   
1610612737  2025-01-25  ATL vs. TOR  L  238   94   33  ...   0.680     8   
1610612737  2025-01-23  ATL vs. TOR  L  240  119   42  ...   0.733     9   
1610612737  2025-01-22  ATL vs. DET  L  241  104   39  ...   0.769    15   
1610612737  2025-01-20    ATL @ NYK  L  239  110   40  ...   0.773    16   
...                ...          ... ..  ...  ...  ...  ...     ...   ...   
1610612766  2024-11-01  CHA vs. BOS  L  241  109   42  ...   0.500    12   
1610612766  2024-10-30  CHA vs. TOR  W  239  138   49  ...   0.800    14   
1610612766  2024-10-26  CHA vs. MIA  L  241  106   39  ...   0.714    15   
1610612766  2024-10-25    CHA @ ATL  L  241  120   37  ...   0.806    22   
1610612766  2024-10-23    CHA @ HOU  W  241  110   38  ...   0.792    15   

            DREB  REB  AST  STL  BLK  TOV  PF  PLUS_MINUS  
TEAM_ID                                                    
1610612737    37   51   24   10    3   21  20        -8.0  
1610612737    35   43   28   14    5   22  20       -23.0  
1610612737    27   36   30   11    2   14  21        -3.0  
1610612737    32   47   25   14    3   13  14       -10.0  
1610612737    25   41   23   10    6   23  21        -9.0  
...          ...  ...  ...  ...  ...  ...  ..         ...  
1610612766    30   42   20    5    5   14  26       -15.0  
1610612766    24   38   31    9    8   15  24         5.0  
1610612766    31   46   20    6    5   17  24        -8.0  
1610612766    31   53   22    7    4   17  28        -5.0  
1610612766    41   56   20    6   10   16  21         5.0  

[1368 rows x 27 columns]

In [ ]:
#Below is the iteration we used to create the script

In [1]:
#this is likely the endpoint we will use:
from nba_api.stats.endpoints import leaguegamefinder
import pandas as pd

# Get all games for a season
game_finder = leaguegamefinder.LeagueGameFinder(
    season_nullable='2023-24',  # Format: YYYY-YY
    league_id_nullable='00',    # 00 is NBA
    season_type_nullable='Regular Season'  # or 'Playoffs'
)

# Convert to DataFrame
games_df = game_finder.get_data_frames()[0]
pd.set_option('display.max_rows', )

games_df

SEASON_ID     TEAM_ID TEAM_ABBREVIATION              TEAM_NAME  \
0        22023  1610612744               GSW  Golden State Warriors   
1        22023  1610612747               LAL     Los Angeles Lakers   
2        22023  1610612756               PHX           Phoenix Suns   
3        22023  1610612749               MIL        Milwaukee Bucks   
4        22023  1610612754               IND         Indiana Pacers   
...        ...         ...               ...                    ...   
2455     22023  1610612764               WAS     Washington Wizards   
2456     22023  1610612747               LAL     Los Angeles Lakers   
2457     22023  1610612743               DEN         Denver Nuggets   
2458     22023  1610612756               PHX           Phoenix Suns   
2459     22023  1610612744               GSW  Golden State Warriors   

         GAME_ID   GAME_DATE      MATCHUP WL  MIN  PTS  ...  FT_PCT  OREB  \
0     0022301198  2024-04-14  GSW vs. UTA  W  239  123  ...   0.826    12   
1     0022301195  2024-04-14    LAL @ NOP  W  241  124  ...   0.944     7   
2     0022301194  2024-04-14    PHX @ MIN  W  244  125  ...   0.833    13   
3     0022301191  2024-04-14    MIL @ ORL  L  238   88  ...   0.913     7   
4     0022301188  2024-04-14  IND vs. ATL  W  239  157  ...   0.800    12   
...          ...         ...          ... ..  ...  ...  ...     ...   ...   
2455  0022300064  2023-10-25    WAS @ IND  L  238  120  ...   0.793    11   
2456  0022300061  2023-10-24    LAL @ DEN  L  239  107  ...   0.750    13   
2457  0022300061  2023-10-24  DEN vs. LAL  W  240  119  ...   0.750     9   
2458  0022300062  2023-10-24    PHX @ GSW  W  241  108  ...   0.765    17   
2459  0022300062  2023-10-24  GSW vs. PHX  L  240  104  ...   0.786    18   

      DREB  REB  AST  STL  BLK  TOV  PF  PLUS_MINUS  
0       30   42   35   10    6    9  14         7.0  
1       32   39   32   12    3   14  13        16.0  
2       19   32   28   13    3   12  24        19.0  
3       27   34   16   10    4   17  18       -25.0  
4       36   48   41   10    6   14  24        42.0  
...    ...  ...  ...  ...  ...  ...  ..         ...  
2455    34   45   28    6    9   14  11       -23.0  
2456    31   44   23    5    4   11  18       -12.0  
2457    33   42   29    9    6   11  15        12.0  
2458    43   60   23    5    7   19  22         4.0  
2459    31   49   19   11    6   11  23        -4.0  

[2460 rows x 28 columns]

In [5]:
import pandas as pd

pd.set_option('display.max_rows', 2460)
games_df

SEASON_ID     TEAM_ID TEAM_ABBREVIATION               TEAM_NAME  \
0        22023  1610612744               GSW   Golden State Warriors   
1        22023  1610612747               LAL      Los Angeles Lakers   
2        22023  1610612756               PHX            Phoenix Suns   
3        22023  1610612749               MIL         Milwaukee Bucks   
4        22023  1610612754               IND          Indiana Pacers   
5        22023  1610612741               CHI           Chicago Bulls   
6        22023  1610612742               DAL        Dallas Mavericks   
7        22023  1610612750               MIN  Minnesota Timberwolves   
8        22023  1610612761               TOR         Toronto Raptors   
9        22023  1610612758               SAC        Sacramento Kings   
10       22023  1610612751               BKN           Brooklyn Nets   
11       22023  1610612739               CLE     Cleveland Cavaliers   
12       22023  1610612737               ATL           Atlanta Hawks   
13       22023  1610612746               LAC             LA Clippers   
14       22023  1610612765               DET         Detroit Pistons   
15       22023  1610612748               MIA              Miami Heat   
16       22023  1610612766               CHA       Charlotte Hornets   
17       22023  1610612760               OKC   Oklahoma City Thunder   
18       22023  1610612738               BOS          Boston Celtics   
19       22023  1610612743               DEN          Denver Nuggets   
20       22023  1610612752               NYK         New York Knicks   
21       22023  1610612757               POR  Portland Trail Blazers   
22       22023  1610612762               UTA               Utah Jazz   
23       22023  1610612755               PHI      Philadelphia 76ers   
24       22023  1610612764               WAS      Washington Wizards   
25       22023  1610612763               MEM       Memphis Grizzlies   
26       22023  1610612753               ORL           Orlando Magic   
27       22023  1610612745               HOU         Houston Rockets   
28       22023  1610612740               NOP    New Orleans Pelicans   
29       22023  1610612759               SAS       San Antonio Spurs   
30       22023  1610612758               SAC        Sacramento Kings   
31       22023  1610612765               DET         Detroit Pistons   
32       22023  1610612744               GSW   Golden State Warriors   
33       22023  1610612742               DAL        Dallas Mavericks   
34       22023  1610612749               MIL         Milwaukee Bucks   
35       22023  1610612751               BKN           Brooklyn Nets   
36       22023  1610612766               CHA       Charlotte Hornets   
37       22023  1610612740               NOP    New Orleans Pelicans   
38       22023  1610612738               BOS          Boston Celtics   
39       22023  1610612739               CLE     Cleveland Cavaliers   
40       22023  1610612756               PHX            Phoenix Suns   
41       22023  1610612755               PHI      Philadelphia 76ers   
42       22023  1610612745               HOU         Houston Rockets   
43       22023  1610612746               LAC             LA Clippers   
44       22023  1610612741               CHI           Chicago Bulls   
45       22023  1610612737               ATL           Atlanta Hawks   
46       22023  1610612747               LAL      Los Angeles Lakers   
47       22023  1610612761               TOR         Toronto Raptors   
48       22023  1610612757               POR  Portland Trail Blazers   
49       22023  1610612764               WAS      Washington Wizards   
50       22023  1610612760               OKC   Oklahoma City Thunder   
51       22023  1610612752               NYK         New York Knicks   
52       22023  1610612753               ORL           Orlando Magic   
53       22023  1610612748               MIA              Miami Heat   
54       22023  1610612754               IND 

In [15]:
games_df = games_df.set_index('TEAM_ID')


KeyError: "None of ['TEAM_ID'] are in the columns"

In [24]:
games_df.loc[1610612744]

SEASON_ID TEAM_ABBREVIATION              TEAM_NAME     GAME_ID  \
TEAM_ID                                                                     
1610612744     22023               GSW  Golden State Warriors  0022301198   
1610612744     22023               GSW  Golden State Warriors  0022301182   
1610612744     22023               GSW  Golden State Warriors  0022301169   
1610612744     22023               GSW  Golden State Warriors  0022301155   
1610612744     22023               GSW  Golden State Warriors  0022301142   
1610612744     22023               GSW  Golden State Warriors  0022301097   
1610612744     22023               GSW  Golden State Warriors  0022301113   
1610612744     22023               GSW  Golden State Warriors  0022300589   
1610612744     22023               GSW  Golden State Warriors  0022301085   
1610612744     22023               GSW  Golden State Warriors  0022301062   
1610612744     22023               GSW  Golden State Warriors  0022301049   
1610612744     22023               GSW  Golden State Warriors  0022301044   
1610612744     22023               GSW  Golden State Warriors  0022301031   
1610612744     22023               GSW  Golden State Warriors  0022301016   
1610612744     22023               GSW  Golden State Warriors  0022301001   
1610612744     22023               GSW  Golden State Warriors  0022300988   
1610612744     22023               GSW  Golden State Warriors  0022300973   
1610612744     22023               GSW  Golden State Warriors  0022300952   
1610612744     22023               GSW  Golden State Warriors  0022300936   
1610612744     22023               GSW  Golden State Warriors  0022300921   
1610612744     22023               GSW  Golden State Warriors  0022300907   
1610612744     22023               GSW  Golden State Warriors  0022300899   
1610612744     22023               GSW  Golden State Warriors  0022300872   
1610612744     22023               GSW  Golden State Warriors  0022300860   
1610612744     22023               GSW  Golden State Warriors  0022300852   
1610612744     22023               GSW  Golden State Warriors  0022300834   
1610612744     22023               GSW  Golden State Warriors  0022300824   
1610612744     22023               GSW  Golden State Warriors  0022300811   
1610612744     22023               GSW  Golden State Warriors  0022300802   
1610612744     22023               GSW  Golden State Warriors  0022300576   
1610612744     22023               GSW  Golden State Warriors  0022300789   
1610612744     22023               GSW  Golden State Warriors  0022300769   
1610612744     22023               GSW  Golden State Warriors  0022300757   
1610612744     22023               GSW  Golden State Warriors  0022300733   
1610612744     22023               GSW  Golden State Warriors  0022300727   
1610612744     22023               GSW  Golden State Warriors  0022300717   
1610612744     22023               GSW  Golden State Warriors  0022300699   
1610612744     22023               GSW  Golden State Warriors  0022300693   
1610612744     22023               GSW  Golden State Warriors  0022300673   
1610612744     22023               GSW  Golden State Warriors  0022300650   
1610612744     22023               GSW  Golden State Warriors  0022300632   
1610612744     22023               GSW  Golden State Warriors  0022300626   
1610612744     22023               GSW  Golden State Warriors  0022300560   
1610612744     22023               GSW  Golden State Warriors  0022300545   
1610612744     22023               GSW  Golden State Warriors  0022300536   
1610612744     22023               GSW  Golden State Warriors  0022300525   
1610612744     22023               GSW  Golden State Warriors  0022300504   
1610612744     22023               GSW  Golden State Warriors  0022300490   
1610612744     22023               GSW  Golden State Warriors  0022300478   
1610612744     22023               GSW  Golden State Warriors  0022300463   
1610612

In [36]:
games_df_sorted = games_df.sort_values(['TEAM_ID', 'GAME_DATE'], ascending=[True, False])

In [38]:
games_df_sorted

SEASON_ID TEAM_ABBREVIATION               TEAM_NAME     GAME_ID  \
TEAM_ID                                                                      
1610612737     22023               ATL           Atlanta Hawks  0022301188   
1610612737     22023               ATL           Atlanta Hawks  0022301178   
1610612737     22023               ATL           Atlanta Hawks  0022301159   
1610612737     22023               ATL           Atlanta Hawks  0022301147   
1610612737     22023               ATL           Atlanta Hawks  0022301130   
1610612737     22023               ATL           Atlanta Hawks  0022301124   
1610612737     22023               ATL           Atlanta Hawks  0022301104   
1610612737     22023               ATL           Atlanta Hawks  0022301091   
1610612737     22023               ATL           Atlanta Hawks  0022301076   
1610612737     22023               ATL           Atlanta Hawks  0022301060   
1610612737     22023               ATL           Atlanta Hawks  0022301051   
1610612737     22023               ATL           Atlanta Hawks  0022301034   
1610612737     22023               ATL           Atlanta Hawks  0022301021   
1610612737     22023               ATL           Atlanta Hawks  0022301010   
1610612737     22023               ATL           Atlanta Hawks  0022300990   
1610612737     22023               ATL           Atlanta Hawks  0022300982   
1610612737     22023               ATL           Atlanta Hawks  0022300966   
1610612737     22023               ATL           Atlanta Hawks  0022300953   
1610612737     22023               ATL           Atlanta Hawks  0022300925   
1610612737     22023               ATL           Atlanta Hawks  0022300913   
1610612737     22023               ATL           Atlanta Hawks  0022300895   
1610612737     22023               ATL           Atlanta Hawks  0022300889   
1610612737     22023               ATL           Atlanta Hawks  0022300866   
1610612737     22023               ATL           Atlanta Hawks  0022300851   
1610612737     22023               ATL           Atlanta Hawks  0022300835   
1610612737     22023               ATL           Atlanta Hawks  0022300821   
1610612737     22023               ATL           Atlanta Hawks  0022300804   
1610612737     22023               ATL           Atlanta Hawks  0022300777   
1610612737     22023               ATL           Atlanta Hawks  0022300763   
1610612737     22023               ATL           Atlanta Hawks  0022300754   
1610612737     22023               ATL           Atlanta Hawks  0022300742   
1610612737     22023               ATL           Atlanta Hawks  0022300729   
1610612737     22023               ATL           Atlanta Hawks  0022300716   
1610612737     22023               ATL           Atlanta Hawks  0022300699   
1610612737     22023               ATL           Atlanta Hawks  0022300690   
1610612737     22023               ATL           Atlanta Hawks  0022300669   
1610612737     22023               ATL           Atlanta Hawks  0022300653   
1610612737     22023               ATL           Atlanta Hawks  0022300634   
1610612737     22023               ATL           Atlanta Hawks  0022300626   
1610612737     22023               ATL           Atlanta Hawks  0022300613   
1610612737     22023               ATL           Atlanta Hawks  0022300595   
1610612737     22023               ATL           Atlanta Hawks  0022300587   
1610612737     22023               ATL           Atlanta Hawks  0022300570   
1610612737     22023               ATL           Atlanta Hawks  0022300559   
1610612737     22023               ATL           Atlanta Hawks  0022300543   
1610612737     22023               ATL           Atlanta Hawks  0022300533   
1610612737     22023               ATL           Atlanta Hawks  0022300521   
1610612737     22023               ATL           Atlanta Hawks  0022300499   
1610612737     22023               ATL           Atlanta Hawks  0022300480   
1610612737     22023             

In [ ]:
#this is likely the endpoint we will use:
from nba_api.stats.endpoints import leaguegamefinder
from sqlalchemy import create_engine
from requests.exceptions import ReadTimeout
import pandas as pd
import random
import time 
import json

#create our engine for pushing to sql database
from dotenv import load_dotenv
import os

load_dotenv()

DATABASE_URL = os.getenv("DATABASE_URL")

engine = create_engine(DATABASE_URL)

#define seasons to gather data for 
seasons = ['2022-23', '2023-24', '2024-25']

for season in seasons:
    try:
        # Get all games for a season
        game_finder = leaguegamefinder.LeagueGameFinder(
            season_nullable=season,  # Format: YYYY-YY
            league_id_nullable='00',    # 00 is NBA
            season_type_nullable='Regular Season'  # or 'Playoffs'
        )
        
        # Convert to DataFrame
        games_df = game_finder.get_data_frames()[0]
        
        #make team ID the index, and sort the dataframe based on ID and gameDate
        games_df = games_df.set_index('TEAM_ID')
        games_df_sorted = games_df.sort_values(['TEAM_ID', 'GAME_DATE'], ascending=[True, False])
    
        #once we've created the dataframe, we want to push that to a SQL database
        filename = f"{season}_historic_game_data"
        games_df_sorted.to_sql(filename, engine, if_exists='replace', index=False)
        print(f"Created and stored dataframe for {season} season")
        print()
        time.sleep(round(random.uniform(3, 6), 1))

    #handle timeout/api rejection errors
    except (ReadTimeout, json.decoder.JSONDecodeError) as e:
        print(f"Error for {season}: {e} - retrying after 60 seconds")
        time.sleep(60)
        continue

print("Finished data gathering for specified seasons")

Created and stored dataframe for 2022-23 season

Created and stored dataframe for 2023-24 season

Created and stored dataframe for 2024-25 season

Finished data gathering for specified seasons


In [51]:
#set display options ot max size 
pd.set_option('display.max_rows', 2460)
pd.set_option('display.max_rows', 55)

games_df_sorted

SEASON_ID TEAM_ABBREVIATION          TEAM_NAME     GAME_ID  \
TEAM_ID                                                                 
1610612737     22024               ATL      Atlanta Hawks  0022400639   
1610612737     22024               ATL      Atlanta Hawks  0022400623   
1610612737     22024               ATL      Atlanta Hawks  0022400612   
1610612737     22024               ATL      Atlanta Hawks  0022400602   
1610612737     22024               ATL      Atlanta Hawks  0022400587   
...              ...               ...                ...         ...   
1610612766     22024               CHA  Charlotte Hornets  0022400132   
1610612766     22024               CHA  Charlotte Hornets  0022400117   
1610612766     22024               CHA  Charlotte Hornets  0022400088   
1610612766     22024               CHA  Charlotte Hornets  0022400079   
1610612766     22024               CHA  Charlotte Hornets  0022400068   

             GAME_DATE      MATCHUP WL  MIN  PTS  FGM  ...  FT_PCT  OREB  \
TEAM_ID                                                ...                 
1610612737  2025-01-25  ATL vs. TOR  L  238   94   33  ...   0.680     8   
1610612737  2025-01-23  ATL vs. TOR  L  240  119   42  ...   0.733     9   
1610612737  2025-01-22  ATL vs. DET  L  241  104   39  ...   0.769    15   
1610612737  2025-01-20    ATL @ NYK  L  239  110   40  ...   0.773    16   
1610612737  2025-01-18    ATL @ BOS  W  265  119   44  ...   0.786    13   
...                ...          ... ..  ...  ...  ...  ...     ...   ...   
1610612766  2024-11-01  CHA vs. BOS  L  241  109   42  ...   0.500    12   
1610612766  2024-10-30  CHA vs. TOR  W  239  138   49  ...   0.800    14   
1610612766  2024-10-26  CHA vs. MIA  L  241  106   39  ...   0.714    15   
1610612766  2024-10-25    CHA @ ATL  L  241  120   37  ...   0.806    22   
1610612766  2024-10-23    CHA @ HOU  W  241  110   38  ...   0.792    15   

            DREB  REB  AST  STL  BLK  TOV  PF  PLUS_MINUS  
TEAM_ID                                                    
1610612737    35   43   28   14    5   22  20       -23.0  
1610612737    27   36   30   11    2   14  21        -3.0  
1610612737    32   47   25   14    3   13  14       -10.0  
1610612737    25   41   23   10    6   23  21        -9.0  
1610612737    42   55   27    9   10   17  17         4.0  
...          ...  ...  ...  ...  ...  ...  ..         ...  
1610612766    30   42   20    5    5   14  26       -15.0  
1610612766    24   38   31    9    8   15  24         5.0  
1610612766    31   46   20    6    5   17  24        -8.0  
1610612766    31   53   22    7    4   17  28        -5.0  
1610612766    41   56   20    6   10   16  21         5.0  

[1344 rows x 27 columns]